In this script, we will import data with article titles, convert those titles into meaningful floating point values of TF * IDF (term frequency * inverse document frequency), then create a linear support vector classifier machine learning model to predict which article titles are fake news. 

In [109]:
import numpy as np 
import pandas as pd 
import matplotlib.pyplot as plt
from matplotlib import style
style.use("ggplot")
from sklearn import svm
from sklearn.model_selection import train_test_split
import math 
from sklearn.svm import SVC
from sklearn.metrics import classification_report, confusion_matrix

We read in two csvs containing the true articles and the fake news articles, add the target column, and merge them. These csvs were downloaded from Kaggle at https://www.kaggle.com/clmentbisaillon/fake-and-real-news-dataset

In [3]:
true_df = pd.read_csv('./True.csv')
fake_df = pd.read_csv('./Fake.csv')

In [4]:
fake_df['target'] = 'fake'
true_df['target'] = 'true'

In [112]:
fake_df

title  \
0       Donald Trump Sends Out Embarrassing New Year’...   
1       Drunk Bragging Trump Staffer Started Russian ...   
2       Sheriff David Clarke Becomes An Internet Joke...   
3       Trump Is So Obsessed He Even Has Obama’s Name...   
4       Pope Francis Just Called Out Donald Trump Dur...   
...                                                  ...   
23476  McPain: John McCain Furious That Iran Treated ...   
23477  JUSTICE? Yahoo Settles E-mail Privacy Class-ac...   
23478  Sunnistan: US and Allied ‘Safe Zone’ Plan to T...   
23479  How to Blow $700 Million: Al Jazeera America F...   
23480  10 U.S. Navy Sailors Held by Iranian Military ...   

                                                    text      subject  \
0      Donald Trump just couldn t wish all Americans ...         News   
1      House Intelligence Committee Chairman Devin Nu...         News   
2      On Friday, it was revealed that former Milwauk...         News   
3      On Christmas day, Donald Trump announced that ...         News   
4      Pope Francis used his annual Christmas Day mes...         News   
...                                                  ...          ...   
23476  21st Century Wire says As 21WIRE reported earl...  Middle-east   
23477  21st Century Wire says It s a familiar theme. ...  Middle-east   
23478  Patrick Henningsen  21st Century WireRemember ...  Middle-east   
23479  21st Century Wire says Al Jazeera America will...  Middle-east   
23480  21st Century Wire says As 21WIRE predicted in ...  Middle-east   

                    date target  
0      December 31, 2017   fake  
1      December 31, 2017   fake  
2      December 30, 2017   fake  
3      December 29, 2017   fake  
4      December 25, 2017   fake  
...                  ...    ...  
23476   January 16, 2016   fake  
23477   January 16, 2016   fake  
23478   January 15, 2016   fake  
23479   January 14, 2016   fake  
23480   January 12, 2016   fake  

[23481 rows x 5 columns]

In [5]:
df = true_df.append(fake_df, ignore_index=True)

In order to convert the title into meaningful floating point values that can predict the target, we must extract the most important words out of the title and add features based on those words. We can do this with nltk. We will tokenize the title, or turn it into an array of words. Then we will remove stopwords, like "the" and "a", that are common and don't contribute to the target. Finally, we use porter stemmer to remove differences in varying prefixes or forms of a word, so that "working" and "works" count as the same word. 

In [6]:
import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem.wordnet import WordNetLemmatizer
from nltk.stem.porter import PorterStemmer

In [7]:
nltk.download('punkt')
nltk.download('stopwords')

[nltk_data] Downloading package punkt to /Users/Seth/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to /Users/Seth/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [8]:
df['title_token'] = df['title'].apply(word_tokenize) 
df['text_token'] = df['text'].apply(word_tokenize) 

In [9]:
stop = stopwords.words('english')
df['title_stop'] = df['title_token'].apply(lambda x: [item for item in x if item not in stop])
df['text_stop'] = df['text_token'].apply(lambda x: [item for item in x if item not in stop])

In [10]:
porter = PorterStemmer()
def stem_sentences(tokens):
    stems = []
    for t in tokens:
        t = t.lower()
        if t.isupper() or t.islower():
            stems.append(porter.stem(t))
    return stems

df['title_stemmed'] = df['title_stop'].apply(stem_sentences)
df['text_stemmed'] = df['text_stop'].apply(stem_sentences)

Next, we will create two dictionaries: 
allWords is a dictionary with keys of every word that occurs in any title, and the value is the number of times it occurred.
wordFreq is a dictionary with keys of every word that occurs in any title, and the value is the number of documents it occurred in. 
We will then reduce wordFreq to the top 

In [89]:
allWords = {}

wordFreq = {}

def BagOfWords(tokens):
    for t in tokens:
        if t not in allWords:
            allWords[t] = 1
        else:
            allWords[t] += 1
    

def perDoc(tokens):
    inDoc = False
    for t in tokens:
        if t in wordFreq:
            if inDoc == False:
                inDoc == True
                wordFreq[t] += 1
        else:
            inDoc = True
            wordFreq[t] = 1
        
    
        
df['title_stemmed'].apply(BagOfWords)    
df['title_stemmed'].apply(perDoc)    

0        None
1        None
2        None
3        None
4        None
         ... 
44893    None
44894    None
44895    None
44896    None
44897    None
Name: title_stemmed, Length: 44898, dtype: object

We then sort allWords, convert it back to a dictionary under the name "test_dict" and then only take the 300 most common words. Then we reduce wordFreq to those same 300 words and save it under the new name "numDocs"

In [33]:
test_arr = sorted(allWords.items(), key=lambda x: x[1], reverse=True)
test_dict = {}
for i in test_arr:
    test_dict[i[0]] = i[1]

In [35]:
import itertools  
test_dict = dict(itertools.islice(test_dict.items(), 300))  

In [93]:
numDocs = {}
for key in test_dict:
    numDocs[key] = wordFreq[key]

Then, we create a copy of our dataframe and add new columns for each of the 300 words. we apply TF which calculates term frequency for every row, for every word column. Next, we will apply IDF and multiply our values out for each word column. Finally, we have the TF * IDF value for every word for each title. Now we're ready to create our machine learning model.

In [24]:
new_df = df

In [38]:
for key in test_dict:
    new_df[key] = 0

In [63]:
def TF(row, keyWord):
    
    doc = row['title_stemmed']
    
    freq = 0
    for word in doc:
        if word == keyWord:
            freq += 1

    numWords = len(doc)
    tf = freq/numWords
    
    return tf

In [66]:
for key in test_dict:
     new_df[key] = new_df.apply(TF, keyWord=key, axis=1)


['as', 'u.s.', 'budget', 'fight', 'loom', 'republican', 'flip', 'fiscal', 'script']
['u.s.', 'militari', 'accept', 'transgend', 'recruit', 'monday', 'pentagon']
['senior', 'u.s.', 'republican', 'senat', "'let", 'mr.', 'mueller', 'job']
['fbi', 'russia', 'probe', 'help', 'australian', 'diplomat', 'tip-off', 'nyt']
['trump', 'want', 'postal', 'servic', 'charg', "'much", 'amazon', 'shipment']
['white', 'hous', 'congress', 'prepar', 'talk', 'spend', 'immigr']
['trump', 'say', 'russia', 'probe', 'fair', 'timelin', 'unclear', 'nyt']
['factbox', 'trump', 'twitter', 'dec', 'approv', 'rate', 'amazon']
['trump', 'twitter', 'dec', 'global', 'warm']
['alabama', 'offici', 'certifi', 'senator-elect', 'jone', 'today', 'despit', 'challeng', 'cnn']
['jone', 'certifi', 'u.s.', 'senat', 'winner', 'despit', 'moor', 'challeng']
['new', 'york', 'governor', 'question', 'constitution', 'feder', 'tax', 'overhaul']
['factbox', 'trump', 'twitter', 'dec', 'vaniti', 'fair', 'hillari', 'clinton']
['trump', 'twitter

['homeland', 'secur', 'nomine', 'say', 'need', 'full', 'u.s.-mexico', 'border', 'wall']
['democrat', 'win', 'bitter', 'virginia', 'governor', "'s", 'race', 'setback', 'trump']
['republican', 'tax', 'bill', 'would', 'add', 'trillion', 'deficit', 'cbo']
['u.s.', 'senat', 'still', 'track', 'releas', 'tax', 'bill', 'thursday', 'aid']
['china', "'s", 'xi', 'fete', 'trump', 'first', 'day', 'beij', 'trip']
['u.s.', 'lawmak', 'introduc', 'bipartisan', 'bill', 'foreign', 'invest', 'amid', 'china', 'worri']
['congress', 'final', 'billion', 'defens', 'spend', 'plan']
['ryan', 'open', 'door', 'later', 'corpor', 'tax', 'rate', 'cut', 'fox', 'news']
['trump', 'warn', "'rogu", 'regim', 'north', 'korea', 'grave', 'danger']
['commerc', 'secretari', 'say', 'trump-xi', 'talk', 'address', 'trade', 'imbal']
['busi', 'group', 'push', 'u.s.', 'flood', 'insur', 'reform', 'decemb', 'deadlin', 'loom']
['white', 'hous', 'condemn', 'missil', 'attack', 'saudi', 'yemen', "'s", 'houthi']
['iran', 'call', 'houthi', '

['trump', 'say', 'wealthi', 'might', 'accept', 'higher', 'tax', 'tax', 'plan']
['trump', 'want', 'work', 'schumer', 'pelosi', 'tax', 'reform', 'white', 'hous']
['trump', 'applaud', 'senat', 'new', 'healthcar', 'reform', 'bill']
['former', 'u.', 'senat', 'pete', 'domenici', 'heavyweight', 'budget', 'energi', 'issu', 'die']
['former', 'trump', 'advis', 'flynn', "'s", 'son', 'probe', 'russia', 'nbc']
['trump', 'administr', 'su', 'phone', 'search', 'u.s.', 'border']
['republican', 'senat', 'cruz', 'push', 'percent', 'corpor', 'tax', 'rate']
['ryan', 'urg', 'daca', 'fix', 'broader', 'immigr', 'reform', 'ap']
['hous', 'speaker', 'ryan', 'leav', 'door', 'open', 'tax', 'deficit']
['factbox', 'trump', 'twitter', 'sept', 'tax', 'reform', 'florida']
['democrat', 'leader', 'schumer', 'pelosi', 'dine', 'trump', 'wednesday']
['tax', 'reform', 'framework', 'appear', 'end-sept.', 'congress', 'sourc']
['ryan', 'say', 'tax', 'reform', 'outlin', 'reflect', 'consensu', 'lawmak', 'administr']
['suprem', 'c

['anthem', 'cut', 'back', 'obamacar', 'plan', 'offer', 'california']
['wray', 'confirm', 'senat', 'lead', 'fbi', 'comey', 'fire']
['tillerson', 'tighten', 'rein', 'state', 'depart']
['democrat', 'want', 'grill', 'well', 'fargo', 'execut', 'auto', 'insur']
['not', 'hallway', 'text', 'committe', 'warn', 'u.s.', 'hous', 'campaign']
['trump', 'fire', 'commun', 'director', 'scaramucci', 'new', 'white', 'hous', 'upheav']
['factbox', 'scaramucci', 'latest', 'leav', 'trump', 'administr']
['trump', 'extol', 'corpor', 'profit', 'seek', 'corpor', 'tax', 'cut']
['senat', 'democrat', 'ron', 'wyden', 'demand', 'justic', 'dept', 'releas', 'new', 'crime', 'reduct', 'polici']
['trump', "'weigh", 'son', "'s", 'russia', 'attorney', 'statement', 'white', 'hous']
['mcconnel', 'say', 'u.s.', 'debt', 'ceil', 'debat', 'could', 'stretch', 'septemb']
['illinoi', 'governor', 'reject', 'school', 'fund', 'legisl']
['senat', 'plan', 'septemb', 'hear', 'health', 'insur', 'market']
['trump', 'administr', 'seek', 'pro

['kremlin', 'deni', 'accus', 'russia', 'tri', 'hack', 'u.s.', 'vote', 'equip']
['top', 'u.s.', 'diplomat', 'china', 'quit', 'trump', 'climat', 'polici']
['white', 'hous', 'want', 'healthcar', 'vote', 'summer', 'tax', 'reform', 'fall']
['trump', 'renew', 'critic', 'london', 'mayor', 'khan', 'attack']
['kellyann', 'conway', "'s", 'husband', 'say', 'trump', 'tweet', 'hurt', 'legal', 'case']
['trump', 'lay', 'plan', 'privat', 'air', 'traffic', 'control', 'system']
['trump', 'block', 'ex-fbi', 'chief', 'comey', "'s", 'testimoni', 'white', 'hous']
['u.s.', 'embassi', 'egypt', 'ban', 'personnel', 'visit', 'religi', 'site', 'outsid', 'cairo']
['panama', "'s", 'presid', 'visit', 'trump', 'white', 'hous', 'june']
['u.s.', 'plan', 'updat', 'self-driv', 'guidelin', 'come', 'month']
['no', 'rehear', 'ex-illinoi', 'governor', 'blagojevich', 'appeal', 'plan']
['trump', 'complic', 'travel', 'ban', 'case', 'grumbl', 'justic', 'depart']
['u.s.', 'top', 'court', 'fault', 'north', 'carolina', 'vote', 'rig

...

['time', 'deport', 'mexican', 'laugh', 'while', 'be', 'sentenc', 'for', 'sodomi', 'kidnap', 'sexual', 'assault', 'in', 'sanctuari', 'state', 'oregon…tel', 'victim', 'rel', 'see', 'all', 'you', 'guy', 'in', 'hell', 'video']
['walmart', 'is', 'sell', 'made', 'in', 'mexico', 'apparel', 'featur', 'domest', 'terror', 'group', 'video']
['flashback', 'to', 'wapo', 'headlin', 'obama', 'should', 'fire', 'john', 'brennan', 'for', 'lying…onli', 'one', 'year', 'after', 'jame', 'clapper', 'wa', 'caught', 'lie', 'under', 'oath']
['abc', 'news', 'get', 'destroy', 'on', 'twitter', 'for', 'wait', 'sever', 'hour', 'to', 'admit', 'they', 'got', 'major', 'detail', 'in', 'flynn', 'stori', 'wrong…', 'fakenewsabc']
['whi', 'is', 'al', 'sharpton', 's', 'half-broth', 'regist', 'thousand', 'of', 'felon', 'to', 'vote', 'in', 'alabama', 'controversi', 'senat', 'race', 'video']
['matt', 'lauer', 'call', 'out', 'by', 'sandra', 'bullock', 'for', 'creepi', 'sex', 'talk', 'dure', 'interview', 'i', 'seen', 'nake', 'vid

['disgust', 'seattl', 'mayor', 'who', 'announc', 'he', 'su', 'trump', 'over', 'sanctuari', 'citi', 'exec', 'order', 'is', 'accus', 'of', 'rape', '15-yr', 'old', 'boy', 'two', 'other']
['sore', 'loser', 'war-hawk', 'john', 'mccain', 'blame', 'presid', 'trump', 'for', 'syrian', 'chemic', 'attack', 'video']
['msnbc', 'pinhead', 'host', 'threaten', 'fox', 's', 'bill', 'o', 'reilli', 'come', 'sue', 'me…i', 'dare', 'video']
['camp', 'nightmar', 'machet', 'wield', 'refuge', 'drag', '23-yr', 'old', 'woman', 'from', 'tent…forc', 'boyfriend', 'to', 'watch', 'the', 'unthink']
['how', 'gorsuch', 'will', 'have', 'immedi', 'effect', 'on', 'histor', '2nd', 'amend', 'decis', 'and', 'these', 'signific', 'controversi', 'case']
['subway', 'rider', 'attack', 'with', 'hammer', 'for', 'ask', 'passeng', 'to', 'stop', 'man-spread']
['paul', 'joseph', 'watson', 'is', 'not', 'happi', 'about', 'the', 'air', 'strike', 'on', 'syria…her', 'whi', 'video']
['watch', 'craze', 'lefti', 'protest', 'trump', 'shut', 'down

['race-bait', 'cop', 'hater', 'dealt', 'major', 'blow', 'baltimor', 'judg', 'find', 'no', 'evid', 'of', 'crime', 'commit', 'against', 'freddi', 'grey']
['break', 'us', 'suprem', 'court', 'rule', 'king', 'obama', 'overstep', 'authority…execut', 'amnesti', 'for', 'million', 'illeg', 'aliens/', 'democrat', 'voter', 'not', 'go', 'to', 'happen']
['boom', 'rep', 'louie', 'gohmert', 'r-tx', 'rip', 'into', 'obama', 'gun', 'grab', 'legisl', 'minion', 'radic', 'islam', 'kill', 'these', 'peopl', 'video']
['break', 'us', 'suprem', 'court', 'uphold', 'u', 'of', 'tx-austin', 'admiss', 'abil', 'to', 'choos', 'black', 'hispan', 'student', 'befor', 'white', 'asian', 'student']
['watch', 'indoctrin', 'colleg', 'student', 'are', 'stun', 'by', 'ugli', 'truth', 'about', 'hillari', 'which', 'candid', 'said']
['flashback', 'hillari', 'receiv', '500k', 'in', 'jewelri', 'from', 'king', 'of', 'barbar', 'nation', 'who', 'brutal', 'oppress', 'women']
['someth', 'wick', 'is', 'happen', 'with', 'refuge', 'in', 'ida

['mainstream', 'media', 'ignor', 'massiv', 'protest', 'against', 'obama', 'sweetheart', 'deal', 'for', 'corpor', 'biggest', 'protest', 'countri', 'seen', 'mani', 'mani', 'year']
['obama', 'tell', 'minut', 'he', 'could', 'win', 'a', 'third', 'term', 'but', 'say', 'he', 'won', 'run…watch', 'surprisingli', 'hard-hit', 'interview', 'here']
['colleg', 'punish', 'success', 'by', 'not', 'allow', 'yacht', 'club', 'at', 'prestigi', 'school', 'video']
['citi', 'across', 'america', 'are', 'replac', 'columbu', 'day', 'with', 'indigen', 'peopl', 'day']
['boycott', 'pro-gun', 'control', 'seth', 'racist', 'rogen', 'star', 'of', 'newli', 'releas', 'steve', 'job', 'movi', 'send', 'vulgar', 'tweet', 'f', 'ck', 'you', 'ben', 'carson']
['rabid', 'pro-amnesti', 'legisl', 'lui', 'gutiérrez', 'on', 'paul', 'ryan', 'for', 'speaker', 'he', 'would', 'work', 'democrat', 'order', 'solv', 'problem', 'america', 'video']
['gq', 'magazin', 'pen', 'repuls', 'articl', 'on', 'brilliant', 'neurosurgeon', 'f', 'ck', 'ben'

['will', 'trumponom', 'bankrupt', 'america']
['the', 'existenti', 'question', 'of', 'whom', 'to', 'trust']
['boiler', 'room', 'did', 'israel', 'attack', 'damascu', 'bill', 'nye', 'the', 'psyop', 'guy']
['the', 'cia', 'doesn', 'need', 'to', 'spi', 'on', 'free', 'thinker', 'the', 'privat', 'sector', 'doe', 'it', 'for', 'free']
['whi', 'not', 'a', 'probe', 'israel-g']
['tax', 'march', 'where', 'were', 'you', 'obama', 'wreck', 'libya']
['mass', 'integr', 'the', 'race', 'capit', 'virtual', 'futur']
['russia-g', 'wa', 'all', 'rage', 'across', 'us', 'media', 'where', 'did', 'go', 'whi']
['boiler', 'room', 'quantum', 'swamp', 'chess']
['easili', 'dupe', 'trump', 'surpass', 'bush', 'fall', 'chemic', 'weapon', 'theatric']
['professor', 'polit', 'ignor', 'go', 'to', 'have', 'consequ']
['is', 'spicer', 'flap', 'cover', 'media', 'tie', 'up', 'white', 'hous', 'global', 'affair', 'scuttl', 'trump', 'domest', 'agenda']
['trump', 'wag', 'dog', 'moment']
['tulsi', 'gabbard', 'trigger', 'the', 'war', 'ha

In [98]:
def IDF(freq):
    return math.log(44898 / freq)

In [99]:
for key in numDocs:
     new_df[key] = new_df[key].apply(lambda x: x*IDF(numDocs[key]))

In [102]:
new_df.describe()

trump         video            to           the           for  \
count  44898.000000  44898.000000  44898.000000  44898.000000  44898.000000   
mean       0.037691      0.026349      0.022378      0.020088      0.016496   
std        0.061454      0.058322      0.055224      0.063119      0.054561   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%        0.000000      0.000000      0.000000      0.000000      0.000000   
50%        0.000000      0.000000      0.000000      0.000000      0.000000   
75%        0.085127      0.000000      0.000000      0.000000      0.000000   
max        0.425635      0.650043      0.462027      0.637369      0.498403   

                 in          u.s.            of            's           say  \
count  44898.000000  44898.000000  44898.000000  44898.000000  44898.000000   
mean       0.016299      0.026978      0.015258      0.025931      0.024450   
std        0.055387      0.086536      0.052941      0.085379      0.080340   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%        0.000000      0.000000      0.000000      0.000000      0.000000   
50%        0.000000      0.000000      0.000000      0.000000      0.000000   
75%        0.000000      0.000000      0.000000      0.000000      0.000000   
max        0.561759      0.712697      0.629066      0.717439      0.627622   

       ...          must    anti-trump        depart        famili  \
count  ...  44898.000000  44898.000000  44898.000000  44898.000000   
mean   ...      0.003152      0.002737      0.003590      0.002893   
std    ...      0.039840      0.035457      0.045645      0.037711   
min    ...      0.000000      0.000000      0.000000      0.000000   
25%    ...      0.000000      0.000000      0.000000      0.000000   
50%    ...      0.000000      0.000000      0.000000      0.000000   
75%    ...      0.000000      0.000000      0.000000      0.000000   
max    ...      0.844450      0.854150      1.027240      0.864449   

            germani          next          most        reveal        defens  \
count  44898.000000  44898.000000  44898.000000  44898.000000  44898.000000   
mean       0.003740      0.003326      0.002513      0.002633      0.003731   
std        0.047959      0.042926      0.032091      0.033922      0.047899   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%        0.000000      0.000000      0.000000      0.000000      0.000000   
50%        0.000000      0.000000      0.000000      0.000000      0.000000   
75%        0.000000      0.000000      0.000000      0.000000      0.000000   
max        1.014759      1.171051      0.856033      0.851058      1.302723   

                big  
count  44898.000000  
mean       0.002864  
std        0.037219  
min        0.000000  
25%        0.000000  
50%        0.000000  
75%        0.000000  
max        1.031064  

[8 rows x 300 columns]

In [72]:
new_df

title  \
0      As U.S. budget fight looms, Republicans flip t...   
1      U.S. military to accept transgender recruits o...   
2      Senior U.S. Republican senator: 'Let Mr. Muell...   
3      FBI Russia probe helped by Australian diplomat...   
4      Trump wants Postal Service to charge 'much mor...   
...                                                  ...   
44893  McPain: John McCain Furious That Iran Treated ...   
44894  JUSTICE? Yahoo Settles E-mail Privacy Class-ac...   
44895  Sunnistan: US and Allied ‘Safe Zone’ Plan to T...   
44896  How to Blow $700 Million: Al Jazeera America F...   
44897  10 U.S. Navy Sailors Held by Iranian Military ...   

                                                    text       subject  \
0      WASHINGTON (Reuters) - The head of a conservat...  politicsNews   
1      WASHINGTON (Reuters) - Transgender people will...  politicsNews   
2      WASHINGTON (Reuters) - The special counsel inv...  politicsNews   
3      WASHINGTON (Reuters) - Trump campaign adviser ...  politicsNews   
4      SEATTLE/WASHINGTON (Reuters) - President Donal...  politicsNews   
...                                                  ...           ...   
44893  21st Century Wire says As 21WIRE reported earl...   Middle-east   
44894  21st Century Wire says It s a familiar theme. ...   Middle-east   
44895  Patrick Henningsen  21st Century WireRemember ...   Middle-east   
44896  21st Century Wire says Al Jazeera America will...   Middle-east   
44897  21st Century Wire says As 21WIRE predicted in ...   Middle-east   

                     date target  \
0      December 31, 2017    true   
1      December 29, 2017    true   
2      December 31, 2017    true   
3      December 30, 2017    true   
4      December 29, 2017    true   
...                   ...    ...   
44893    January 16, 2016   fake   
44894    January 16, 2016   fake   
44895    January 15, 2016   fake   
44896    January 14, 2016   fake   
44897    January 12, 2016   fake   

                                             title_token  \
0      [As, U.S., budget, fight, looms, ,, Republican...   
1      [U.S., military, to, accept, transgender, recr...   
2      [Senior, U.S., Republican, senator, :, 'Let, M...   
3      [FBI, Russia, probe, helped, by, Australian, d...   
4      [Trump, wants, Postal, Service, to, charge, 'm...   
...                                                  ...   
44893  [McPain, :, John, McCain, Furious, That, Iran,...   
44894  [JUSTICE, ?, Yahoo, Settles, E-mail, Privacy, ...   
44895  [Sunnistan, :, US, and, Allied, ‘, Safe, Zone,...   
44896  [How, to, Blow, $, 700, Million, :, Al, Jazeer...   
44897  [10, U.S., Navy, Sailors, Held, by, Iranian, M...   

                                              text_token  \
0      [WASHINGTON, (, Reuters, ), -, The, head, of, ...   
1      [WASHINGTON, (, Reuters, ), -, Transgender, pe...   
2      [WASHINGTON, (, Reuters, ), -, The, special, c...   
3      [WASHINGTON, (, Reuters, ), -, Trump, campaign...   
4      [SEATTLE/WASHINGTON, (, Reuters, ), -, Preside...   
...                                                  ...   
44893  [21st, Century, Wire, says, As, 21WIRE, report...   
44894  [21st, Century, Wire, says, It, s, a, familiar...   
44895  [Patrick, Henningsen, 21st, Century, WireRemem...   
44896  [21st, Century, Wire, says, Al, Jazeera, Ameri...   
44897  [21st, Century, Wire, says, As, 21WIRE, predic...   

                                              title_stop  \
0      [As, U.S., budget, fight, looms, ,, Republican...   
1      [U.S., military, accept, transgender, recruits...   
2      [Senior, U.S., Republican, senator, :, 'Let, M...   
3      [FBI, Russia, probe, helped, Australian, diplo...   
4      [Trump, wants, Postal, Service, charge, 'much,...   
...                                                  ...   
44893  [McPain, :, John, McCain, Furious, That, Iran,...   
44894  [JUSTICE, ?, Yahoo, Settles, E-mail, Privacy, ...   
44895  [Sunnistan, :, US, 

Finally, we'll train a linear support vector classifier model to predict fake or true news if given the title of a new unseen article. We'll separate our dataframe with 80% for the test set and 20% for the training set. Then, we run the model, and print the confusion matrix to see how it did!

In [57]:
from sklearn import svm
from sklearn.model_selection import train_test_split
import math 

In [56]:
def convertTarget(x):
    if x == 'fake':
        return 1
    else:
        return 0

In [104]:
new_df['target'] = new_df['target'].apply(lambda x: convertTarget(x))

X = new_df.drop(['target', 'title', 'text', 'subject', 'date', 'title_token', 'text_token', 'title_stop', 'text_stop', 'title_stemmed', 'text_stemmed'], axis=1)
y = new_df['target']

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.20)


In [107]:
svclassifier = SVC(kernel='linear')
svclassifier.fit(X_train, y_train)

SVC(C=1.0, cache_size=200, class_weight=None, coef0=0.0,
    decision_function_shape='ovr', degree=3, gamma='auto_deprecated',
    kernel='linear', max_iter=-1, probability=False, random_state=None,
    shrinking=True, tol=0.001, verbose=False)

In [110]:
y_pred = svclassifier.predict(X_test)

print(confusion_matrix(y_test,y_pred))
print(classification_report(y_test,y_pred))

[[4164  111]
 [ 210 4495]]
              precision    recall  f1-score   support

           0       0.95      0.97      0.96      4275
           1       0.98      0.96      0.97      4705

    accuracy                           0.96      8980
   macro avg       0.96      0.96      0.96      8980
weighted avg       0.96      0.96      0.96      8980



As can be seen above, the model had high precision when predicting that an article was fake news. 98% accurate, in fact! This is what we want. In the application of this model, you would prefer to miss a few fake news articles than incorrectly label a true news article as fake, as that would lose credibility. 

Social media giants that are dealing with public pressure to label fake news are in need of machine learning algorithms to help them identify fake news based only on the title of the article. This model could have a huge impact and make it much harder for misinformation to affect elections and public perception of varying issues. 